In [2]:
# importing libraries

import pandas as pd
from datasets import load_dataset

import torch
from transformers import AutoTokenizer, Trainer, TrainingArguments, DefaultDataCollator, AutoModelForQuestionAnswering


In [2]:
# download and load the dataset splitting intor train and test set. Here only number of dataset is limited to 5000 
squad = load_dataset("squad")

In [3]:
squad

DatasetDict({
    train: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 87599
    })
    validation: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 10570
    })
})

In [4]:
squad

DatasetDict({
    train: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 87599
    })
    validation: Dataset({
        features: ['id', 'title', 'context', 'question', 'answers'],
        num_rows: 10570
    })
})

In [5]:
# Print the top 5 rows
for i in range(5):
    print(squad["train"][i])

{'id': '5733be284776f41900661182', 'title': 'University_of_Notre_Dame', 'context': 'Architecturally, the school has a Catholic character. Atop the Main Building\'s gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.', 'question': 'To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?', 'answers': {'text': ['Saint Bernadette Soubirous'], 'answer_start': [515]}}
{'id': '5733be284776f4190066117f', 'title': 'Universit

### several important fields 
<li>answers: the starting location of the answer token and the answer text. </li>
<li>context: background information from which the model needs to extract the answer. </li>
<li>question: the question a model should answer. </li>

In [6]:
tokenizer = AutoTokenizer.from_pretrained("distilbert-base-uncased")

## Preprocessing Steps for Question Answering Tasks

### Dealing with Long Contexts

Some examples in a dataset may have a very long context that exceeds the maximum input length of the model. To address this:

- Truncate only the context by setting `truncation="only_second"`.

### Mapping Answer Positions to Original Context

To map the start and end positions of the answer to the original context:

- Set `return_offset_mapping=True` during tokenization.

### Finding Start and End Tokens of the Answer

With the offset mapping, use the following steps to find the start and end tokens of the answer:

- Utilize the `sequence_ids` method to determine which part of the offset corresponds to the question and which corresponds to the context.

In [7]:
def preprocess_function(examples):
    questions = [q.strip() for q in examples["question"]]
    inputs = tokenizer(
        questions,
        examples["context"],
        max_length=384,
        truncation="only_second",
        return_offsets_mapping=True,
        padding="max_length",
    )

    offset_mapping = inputs.pop("offset_mapping")
    answers = examples["answers"]
    start_positions = []
    end_positions = []

    for i, offset in enumerate(offset_mapping):
        answer = answers[i]
        start_char = answer["answer_start"][0]
        end_char = answer["answer_start"][0] + len(answer["text"][0])
        sequence_ids = inputs.sequence_ids(i)

        # Find the start and end of the context
        idx = 0
        while sequence_ids[idx] != 1:
            idx += 1
        context_start = idx
        while sequence_ids[idx] == 1:
            idx += 1
        context_end = idx - 1

        # If the answer is not fully inside the context, label it (0, 0)
        if offset[context_start][0] > end_char or offset[context_end][1] < start_char:
            start_positions.append(0)
            end_positions.append(0)
        else:
            # Otherwise it's the start and end token positions
            idx = context_start
            while idx <= context_end and offset[idx][0] <= start_char:
                idx += 1
            start_positions.append(idx - 1)

            idx = context_end
            while idx >= context_start and offset[idx][1] >= end_char:
                idx -= 1
            end_positions.append(idx + 1)

    inputs["start_positions"] = start_positions
    inputs["end_positions"] = end_positions
    return inputs

In [8]:
# applying preprocessing function to entire dataset
tokenized_datasets = squad.map(preprocess_function, batched=True)

Map:   0%|          | 0/87599 [00:00<?, ? examples/s]

Map: 100%|██████████| 10570/10570 [00:02<00:00, 4331.36 examples/s]


In [9]:
tokenized_datasets['train'][0]

{'id': '5733be284776f41900661182',
 'title': 'University_of_Notre_Dame',
 'context': 'Architecturally, the school has a Catholic character. Atop the Main Building\'s gold dome is a golden statue of the Virgin Mary. Immediately in front of the Main Building and facing it, is a copper statue of Christ with arms upraised with the legend "Venite Ad Me Omnes". Next to the Main Building is the Basilica of the Sacred Heart. Immediately behind the basilica is the Grotto, a Marian place of prayer and reflection. It is a replica of the grotto at Lourdes, France where the Virgin Mary reputedly appeared to Saint Bernadette Soubirous in 1858. At the end of the main drive (and in a direct line that connects through 3 statues and the Gold Dome), is a simple, modern stone statue of Mary.',
 'question': 'To whom did the Virgin Mary allegedly appear in 1858 in Lourdes France?',
 'answers': {'text': ['Saint Bernadette Soubirous'], 'answer_start': [515]},
 'input_ids': [101,
  2000,
  3183,
  2106,
  1996

In [10]:
# creating a batch of examples using DefaultDataCollator
data_collator = DefaultDataCollator()

In [11]:
# loading pre-trained model
model = AutoModelForQuestionAnswering.from_pretrained("distilbert-base-uncased")


Some weights of DistilBertForQuestionAnswering were not initialized from the model checkpoint at distilbert-base-uncased and are newly initialized: ['qa_outputs.weight', 'qa_outputs.bias']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [16]:
# fine tuning the distilber-base-uncased model

training_args = TrainingArguments(
    output_dir="finetuning_squad",
    evaluation_strategy="epoch",
    learning_rate=2e-5,
    per_device_train_batch_size=16,
    per_device_eval_batch_size=16,
    num_train_epochs=3,
    weight_decay=0.01,
)

trainer = Trainer(
    model=model,
    args=training_args,
    train_dataset=tokenized_datasets['train'],
    eval_dataset=tokenized_datasets['validation'],
    tokenizer=tokenizer,
    data_collator=data_collator,
)


In [17]:
trainer.train()

  0%|          | 0/4107 [00:53<?, ?it/s]
                                                     
  3%|▎         | 500/16425 [02:27<1:18:36,  3.38it/s]

{'loss': 2.9417, 'learning_rate': 1.9391171993911722e-05, 'epoch': 0.09}


                                                      
  6%|▌         | 1000/16425 [04:54<1:13:37,  3.49it/s]

{'loss': 1.7699, 'learning_rate': 1.8782343987823442e-05, 'epoch': 0.18}


                                                      
  9%|▉         | 1500/16425 [07:18<1:10:45,  3.52it/s]

...

                                                       
 97%|█████████▋| 16000/16425 [1:16:46<01:54,  3.70it/s]

{'loss': 0.7728, 'learning_rate': 5.17503805175038e-07, 'epoch': 2.92}


100%|██████████| 16425/16425 [1:18:46<00:00,  3.48it/s]





















































































































































































































































































































































                                                       
                                       

100%|██████████| 16425/16425 [1:19:51<00:00,  3.48it/s]

                                                       
100%|██████████| 16425/16425 [1:19:51<00:00,  3.43it/s]

{'eval_loss': 1.1455239057540894, 'eval_runtime': 64.9253, 'eval_samples_per_second': 162.802, 'eval_steps_per_second': 10.181, 'epoch': 3.0}
{'train_runtime': 4791.8158, 'train_samples_per_second': 54.843, 'train_steps_per_second': 3.428, 'train_loss': 1.0782835241866437, 'epoch': 3.0}


TrainOutput(global_step=16425, training_loss=1.0782835241866437, metrics={'train_runtime': 4791.8158, 'train_samples_per_second': 54.843, 'train_steps_per_second': 3.428, 'train_loss': 1.0782835241866437, 'epoch': 3.0})

In [6]:
question = "how many parameters in bloom?"
context = "BLOOM has 176 billion parameters and can generate text in 46 languages natural languages and 13 programming languages."

In [7]:
from transformers import pipeline
question_answerer = pipeline("question-answering", model="finetuning_squad/checkpoint-16000")
question_answerer(question=question, context=context)

{'score': 0.8450772762298584, 'start': 10, 'end': 21, 'answer': '176 billion'}